#  ## ETL Project

In [1]:
# Dependency
import pandas as pd
import sqlalchemy
from sqlalchemy import create_engine
import os
import json
import pymysql
pymysql.install_as_MySQLdb()
from config import mypass

### Store filterd CSV into DataFrame 

In [2]:
# Loading extracted CSV file for list of Active businee in LA
trimmied_csv_file = "trimmed-list-of-active-businesses.csv"
active_businesses_df = pd.read_csv(trimmied_csv_file, encoding='utf-8')
active_businesses_df.head()

BUSINESS NAME  \
0                                   VINCENZO LABELLA   
1      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   
2  SPRINGBOARD NON-PROFIT CONSUMER CREDIT MANAGEMENT   
3      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   
4      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   

              STREET ADDRESS               CITY    ZIP CODE  
0      521 SWARTHMORE AVENUE  PACIFIC PALISADES  90272-4350  
1       2015 W TEMPLE STREET        LOS ANGELES  90026-4913  
2  1605 W OLYMPIC BLVD #9023        LOS ANGELES  90015-3828  
3           3806 W PICO BLVD        LOS ANGELES  90019-4304  
4           3115 VENICE BLVD        LOS ANGELES  90019-6238

In [3]:
# checking the tble properties
list(active_businesses_df)

['BUSINESS NAME', 'STREET ADDRESS', 'CITY', 'ZIP CODE']

In [4]:
active_businesses_df.count()

BUSINESS NAME     14999
STREET ADDRESS    14998
CITY              14999
ZIP CODE          14999
dtype: int64

In [5]:
active_businesses_df.describe()

BUSINESS NAME  \
count                                  14999   
unique                                 14815   
top     VOLUNTEERS OF AMERICA OF LOS ANGELES   
freq                                      18   

                           STREET ADDRESS         CITY    ZIP CODE  
count                               14998        14999       14999  
unique                              14739          438       13741  
top     11812 SAN VICENTE BLVD FLOOR #4TH  LOS ANGELES  90046-2401  
freq                                    7         7494          10

In [6]:
active_businesses_df = active_businesses_df.dropna(how='any')
active_businesses_df.count()

BUSINESS NAME     14998
STREET ADDRESS    14998
CITY              14998
ZIP CODE          14998
dtype: int64

### Store JSON data into a DataFrame

In [7]:
# Loading json file for bike data

with open('bikes.json') as json_data:
   data = json.load(json_data)


print(json.dumps(data, indent=4, sort_keys=True))


{
    "features": [
        {
            "geometry": {
                "coordinates": [
                    -118.25854,
                    34.0485
                ],
                "type": "Point"
            },
            "properties": {
                "addressCity": "Los Angeles",
                "addressState": "CA",
                "addressStreet": "723 Flower Street",
                "addressZipCode": "90017",
                "bikesAvailable": 21,
                "classicBikesAvailable": 21,
                "closeTime": "23:58:00",
                "docksAvailable": 4,
                "electricBikesAvailable": 0,
                "eventEnd": null,
                "eventStart": null,
                "hasGeofence": false,
                "isEventBased": false,
                "isVirtual": false,
                "isVisible": false,
                "kioskConnectionStatus": "Active",
                "kioskId": 3005,
                "kioskPublicStatus": "Active",
                "kio

In [8]:
# setting variables

Address = []
Names = []
city = []
zip_code = []
features = data["features"]
for feature in features:
   Address.append(feature["properties"]["addressStreet"])
   Names.append(feature["properties"]["name"])
   city.append(feature["properties"]["addressCity"])
   zip_code.append(feature["properties"]["addressZipCode"])

print(Address)
print(len(Address))
print(Names)
print(len(Names))
print(city)
print(len(city))
print(zip_code)
print(len(zip_code))

['723 Flower Street', '729 S Olive Street', '557 S 5th Street', '865 S Figueroa Street', '401 East 11th Street', '1259-1299 S Figueroa Street', '128 W Anaheim St', '834 N Alameda St', '201 N Los Angeles Street', '919 S Grand Ave', '129 W 12th Street', '1950 S Hill Street', '999 E Third Street', '134 Judge John Aiso Street', '111 N Hope Street', '1014 S Grand Ave', '668 N Figueroa Street', '300 S Spring Street', '310 N Grand Ave', '334 S Main Street', '120 S Main Street', '201 W 7th Street', '557 S Hope Street', '110 E 9th Street', '1113 S Hope St', '735 S Figueroa Street', '1301 Willow Street', '699 S Imperial St', '458 S Main Street', '1234 Wilshire Blvd', '369 E First Street', '1850 San Pedro St', '201 South Hill Street', '515 W Pico Street', '1210 East 5th Street', '945 W 2nd Street', '307 W 7th Street', '1107 W 7th Street', '1245 Factory Place', '1375 S Grand Ave', '512 W 18th Street', '1855 Industrial Street', '350 E Third Street', '532 W Olive Street', '700 S Grand Ave', '725 New

In [9]:
# displaying json data to data frame
bike_data_df = pd.DataFrame({"Address":Address, "Location_Name":Names,"addressCity":city,"ZipCode":zip_code})
bike_data_df.head()

Address   Location_Name  addressCity ZipCode
0      723 Flower Street    7th & Flower  Los Angeles   90017
1     729 S Olive Street     Olive & 8th  Los Angeles   90014
2       557 S 5th Street     5th & Grand  Los Angeles   90071
3  865 S Figueroa Street  Figueroa & 9th  Los Angeles   90017
4   401 East 11th Street    11th & Maple  Los Angeles   90015

### Connect to local database

In [10]:
connection_string = f"root:{mypass}@127.0.0.1/ETL_DB"
engine = create_engine(f'mysql://{connection_string}')

### Check for tables

In [11]:
engine.table_names()

['bike', 'business']

### Use pandas to load json converted DataFrame into database

In [12]:
bike_data_df.to_sql(name='bike',con=engine,if_exists='append',index=False)

### Use pandas to load csv converted DataFrame into database

In [13]:
active_businesses_df.to_sql(name='business',con=engine,if_exists='append',index=False)

InternalError: (pymysql.err.InternalError) (1054, "Unknown column 'BUSINESS NAME' in 'field list'") [SQL: 'INSERT INTO business (`BUSINESS NAME`, `STREET ADDRESS`, `CITY`, `ZIP CODE`) VALUES (%(BUSINESS NAME_m0)s, %(STREET ADDRESS_m0)s, %(CITY_m0)s, %(ZIP CODE_m0)s), (%(BUSINESS NAME_m1)s, %(STREET ADDRESS_m1)s, %(CITY_m1)s, %(ZIP CODE_m1)s), (%(BUSINESS NAME_m2)s, %(STREET ADDRESS_m2)s, %(CITY_m2)s, %(ZIP CODE_m2)s), (%(BUSINESS NAME_m3)s, %(STREET ADDRESS_m3)s, %(CITY_m3)s, %(ZIP CODE_m3)s), (%(BUSINESS NAME_m4)s, %(STREET ADDRESS_m4)s, %(CITY_m4)s, %(ZIP CODE_m4)s), (%(BUSINESS NAME_m5)s, %(STREET ADDRESS_m5)s, %(CITY_m5)s, %(ZIP CODE_m5)s), (%(BUSINESS NAME_m6)s, %(STREET ADDRESS_m6)s, %(CITY_m6)s, %(ZIP CODE_m6)s), (%(BUSINESS NAME_m7)s, %(STREET ADDRESS_m7)s, %(CITY_m7)s, %(ZIP CODE_m7)s), (%(BUSINESS NAME_m8)s, %(STREET ADDRESS_m8)s, %(CITY_m8)s, %(ZIP CODE_m8)s), (%(BUSINESS NAME_m9)s, %(STREET ADDRESS_m9)s, %(CITY_m9)s, %(ZIP CODE_m9)s), (%(BUSINESS NAME_m10)s, %(STREET ADDRES

### Confirm data has been added by querying the business table


In [14]:
pd.read_sql_query('select * from business',con=engine).head()

id                                      business_name  \
0   1                                   VINCENZO LABELLA   
1   2      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   
2   3  SPRINGBOARD NON-PROFIT CONSUMER CREDIT MANAGEMENT   
3   4      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   
4   5      A A OFICINA CENTRAL HISPANA DE LOS ANGELES /C   

                      street               city    zip_code  
0      521 SWARTHMORE AVENUE  PACIFIC PALISADES  90272-4350  
1       2015 W TEMPLE STREET        LOS ANGELES  90026-4913  
2  1605 W OLYMPIC BLVD #9023        LOS ANGELES  90015-3828  
3           3806 W PICO BLVD        LOS ANGELES  90019-4304  
4           3115 VENICE BLVD        LOS ANGELES  90019-6238

### Confirm data has been added by querying the bike table

In [15]:
pd.read_sql_query('select * from bike',con=engine).head()

id                Address   Location_Name  addressCity  ZipCode
0   1      723 Flower Street    7th & Flower  Los Angeles  90017.0
1   2     729 S Olive Street     Olive & 8th  Los Angeles  90014.0
2   3       557 S 5th Street     5th & Grand  Los Angeles  90071.0
3   4  865 S Figueroa Street  Figueroa & 9th  Los Angeles  90017.0
4   5   401 East 11th Street    11th & Maple  Los Angeles  90015.0